In [5]:
# Import necessary libraries
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import matplotlib.pyplot as plt
from plotly.subplots import make_subplots
from datetime import datetime, timedelta
from statsmodels.tsa.seasonal import STL
from statsmodels.tsa.seasonal import seasonal_decompose
from scipy.signal import find_peaks
from sklearn.metrics import mean_squared_error
from pmdarima import auto_arima
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
import seaborn as sns
import xgboost as xgb
import pandas_datareader.data as web
import datetime
import yfinance as yf
from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly

In [6]:
# Gold price api
gold = yf.download('GC=F', start='2000-01-01', end='2026-02-20', multi_level_index=False, progress = False, auto_adjust=True)['Close']
gold.to_csv('gold_price_daily.csv')
gold = gold.to_frame()
gold.index = pd.to_datetime(gold.index)

In [7]:
# Gold price plots
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Gold price 2000-2026', ' year-to-year cumulative return')
)

# left graph
fig.add_trace(
    go.Scatter(
        x=gold.index,
        y=gold['Close'],
        mode='lines',
        line=dict(color='rgba(0, 255, 255, 1)') # Neon cyan
    ),
    row=1, col=1
)

# Add year-to-year cumulative return

df_year = gold.groupby(gold.index.strftime('%Y')).tail(1).reset_index(drop=True) # Record the last day of each year
df_year['Cumulative_Return'] = (df_year['Close'] - df_year.iloc[0]['Close']) / df_year.iloc[0]['Close']

fig.add_trace(
    go.Scatter(
        x=df_year.index,
        y=df_year['Cumulative_Return'],
        mode='lines',
        line=dict(color='rgba(255, 20, 147, 1)'), # Neon pink
        marker=dict(size=8, color='rgba(255, 20, 147, 1)')
    ),
    row=1, col=2
)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=False,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="US dollar", col=1)
fig.update_yaxes(title_text="times", col=2)

fig.show()


In [8]:
# STL decomposition and peak detection

df_month = gold.resample('ME').last().reset_index()  # Resample to monthly frequency using the last day of each month
ts = df_month.set_index('Date')['Close']
stl = STL(ts, period=12)
result = stl.fit()

trend = result.trend
seasonality = result.seasonal
shock = result.resid

# Find peaks in seasonality

# prominence → how much the peak stands out from surroundings
# distance → minimum spacing between peaks

std = seasonality.std()

MIN_PROMINENCE = std * 1.0
MIN_DISTANCE = 6             # minimum ~6 months between peaks

# High peaks
high_peaks, high_props = find_peaks(
    seasonality,
    prominence=MIN_PROMINENCE,
    distance=MIN_DISTANCE
)

# Low peaks
low_peaks, low_props = find_peaks(
    -seasonality,
    prominence=MIN_PROMINENCE,
    distance=MIN_DISTANCE
)

# Extract peak months
seasonality_index = seasonality.index
month_dict = {1: 'Jan', 2: 'Feb', 3: 'Mar', 4: 'Apr', 5: 'May', 6: 'Jun',
              7: 'Jul', 8: 'Aug', 9: 'Sep', 10: 'Oct', 11: 'Nov', 12: 'Dec'}
high_peak_months = pd.to_datetime(seasonality_index[high_peaks]).month
low_peak_months = pd.to_datetime(seasonality_index[low_peaks]).month

# Count peaks per month

month_order = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun',
               'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']

high_peak_counts = (
    pd.Series(high_peak_months)
    .map(month_dict)
    .value_counts()
    .reindex(month_order, fill_value=0)
)

low_peak_counts = (
    pd.Series(low_peak_months)
    .map(month_dict)
    .value_counts()
    .reindex(month_order, fill_value=0)
)

fig = make_subplots(
    rows=5, cols=1,
    subplot_titles=(
        'Gold Price',
        'Trend',
        'Seasonality (12-month period)',
        'Shock',
        'Low and High Peaks by Month'
    ),
    vertical_spacing=0.05,
    row_heights=[0.30, 0.18, 0.18, 0.18, 0.16]
)

# Price
fig.add_trace(
    go.Scatter(x=ts.index, y=ts, name='Price', line=dict(color='rgba(0, 255, 255, 1)')),
    row=1, col=1
)

# Trend
fig.add_trace(
    go.Scatter(x=ts.index, y=trend, name='Trend', line=dict(color='lime')),
    row=2, col=1
)

# Seasonality
fig.add_trace(
    go.Scatter(x=ts.index, y=seasonality, name='Seasonality', line=dict(color='gray')),
    row=3, col=1
)

fig.add_trace(
    go.Scatter(
        x=seasonality_index[high_peaks],
        y=seasonality.iloc[high_peaks],
        mode='markers',
        marker=dict(color='green', size=10, symbol='triangle-up'),
        name='High Peaks'
    ),
    row=3, col=1
)
fig.add_trace(
    go.Scatter(
        x=seasonality_index[low_peaks],
        y=seasonality.iloc[low_peaks],
        mode='markers',
        marker=dict(color='red', size=10, symbol='triangle-down'),
        name='Low Peaks'
    ),
    row=3, col=1
)

# Shock
fig.add_trace(
    go.Scatter(x=ts.index, y=shock, name='Shock', line=dict(color='pink')),
    row=4, col=1
)

# Monthly low-high peak counts bar chart
fig.add_trace(
    go.Bar(
        x=high_peak_counts.index,
        y=high_peak_counts.values,
        name="High Peaks",
        marker_color="green"
    ),
    row=5, col=1
)

fig.add_trace(
    go.Bar(
        x=low_peak_counts.index,
        y=low_peak_counts.values,
        name="Low Peaks",
        marker_color="red"
    ),
    row=5, col=1
)

# Layout
fig.update_layout(
    height=1200,
    width=1200,
    showlegend=False,
    template='plotly_dark'
)

# Labels
fig.update_yaxes(title_text="Price", row=1)
fig.update_yaxes(title_text="Trend", row=2)
fig.update_yaxes(title_text="Seasonal", row=3)
fig.update_yaxes(title_text="Shock", row=4)
fig.update_yaxes(title_text="Peak Counts", row=5)

fig.show()



### XGBOOST

In [9]:
# Predict 180 days ahead return
df_xg = gold.copy()

In [10]:
# Fetch external macro indicators from Yahoo Finance and FRED

yh_tickers = ['^GSPC', '^VIX', 'DX-Y.NYB']
yf_data = yf.download(yh_tickers, start="2000-01-01", end="2026-02-20", progress=False, multi_level_index=False, auto_adjust=True)['Close']
yf_data.to_csv('macro_indicators_yf.csv')
name_map = {
    'DX-Y.NYB': 'dollar',
    '^GSPC': 'sp500',
    '^VIX': 'vix'
}
yf_data = yf_data.rename(columns=name_map)

fred_tickers = ['DGS10', 'CPIAUCSL', 'DCOILWTICO']
fred_df = web.DataReader(fred_tickers, 'fred', datetime.datetime(2000, 1, 1), datetime.datetime(2026, 2, 20))
fred_df['CPIAUCSL'] = fred_df['CPIAUCSL'].ffill()
fred_df.to_csv('macro_indicators_fred.csv')

df_xg = df_xg.merge(yf_data, left_index=True, right_index=True, how='left')
df_xg = df_xg.merge(fred_df, left_index=True, right_index=True, how='left')


In [11]:
# Plot macro indicators
fig = make_subplots(
    rows=6, cols=1,
    subplot_titles=('Macroeconomic indicators',)
    
)

#crude oil
fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['DCOILWTICO'],
        mode='lines',
        name='Crude Oil Price',
        line=dict(color='green') 
    ),
    row=1, col=1 )

#stock market
fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['sp500'],
        mode='lines',
        name='GSPC (S&P 500 Index)'
    ),
    row=2, col=1)

#dollar
fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['dollar'],
        mode='lines',
        name='DXY (US Dollar Index)',
        line=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=3, col=1)

#volatility
fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['vix'],
        mode='lines',
        name='VIX (Volatility Index)'
    ),
    row=4, col=1)

#interest rate
fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['DGS10'],
        mode='lines',
        name='DGS10 (10-Year Treasury Yield)'
    ),
    row=5, col=1)

#consumer price index
fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['CPIAUCSL'],
        mode='lines',
        name='CPIAUCSL (Consumer Price Index)'
    ),
    row=6, col=1)

# Update layout
fig.update_layout(
    height=800,
    width=1200,
    showlegend=True,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="oil", row=1)
fig.update_yaxes(title_text="sp500", row=2)
fig.update_yaxes(title_text="dollar", row=3)
fig.update_yaxes(title_text="vix", row=4)
fig.update_yaxes(title_text="r0", row=5)
fig.update_yaxes(title_text="cpi", row=6)
fig.show()

In [12]:
# Feature engineer

#LAG FEATURES
lags = [1,2,3,5,10,20,50,100,180,365]

for lag in lags:
    df_xg[f'lag_close_{lag}'] = df_xg['Close'].shift(lag)
    df_xg[f'lag_return_{lag}'] = df_xg['Close'].shift(lag) / df_xg['Close'].shift(lag+1) - 1

# MOVING AVERAGES FEATURES
windows = [7,30,90,180,365]

for w in windows:
    df_xg[f'MA_{w}'] = df_xg['Close'].shift(1).rolling(w).mean()
    df_xg[f'EMA_{w}'] = df_xg['Close'].shift(1).ewm(span=w).mean()

# TREND FEATURES
df_xg['trend_7_30'] = df_xg['MA_7'] - df_xg['MA_30']
df_xg['trend_30_365'] = df_xg['MA_30'] - df_xg['MA_365']
df_xg['price_vs_MA30'] = df_xg['Close'].shift(1) / df_xg['MA_30'] - 1
df_xg['price_vs_MA365'] = df_xg['Close'].shift(1) / df_xg['MA_365'] - 1

# MOMENTUM FEATURES
df_xg['momentum_7'] = df_xg['Close'].shift(1) / df_xg['Close'].shift(7) - 1
df_xg['momentum_30'] = df_xg['Close'].shift(1) / df_xg['Close'].shift(30) - 1
df_xg['momentum_90'] = df_xg['Close'].shift(1) / df_xg['Close'].shift(90) - 1
df_xg['momentum_180'] = df_xg['Close'].shift(1) / df_xg['Close'].shift(180) - 1
df_xg['momentum_365'] = df_xg['Close'].shift(1) / df_xg['Close'].shift(365) - 1

# VOLATILITY FEATURES
df_xg['return_1'] = df_xg['Close'].pct_change().shift(1)
df_xg['volatility_7'] = df_xg['return_1'].rolling(7).std()
df_xg['volatility_30'] = df_xg['return_1'].rolling(30).std()
df_xg['volatility_90'] = df_xg['return_1'].rolling(90).std()
df_xg['volatility_180'] = df_xg['return_1'].rolling(180).std()

# RSI: Relative Strength Index
delta = df_xg['Close'].diff()
gain = delta.where(delta > 0, 0)
loss = -delta.where(delta < 0, 0)
avg_gain = gain.ewm(alpha=1/14, min_periods=14, adjust=False).mean()
avg_loss = loss.ewm(alpha=1/14, min_periods=14, adjust=False).mean()
rs = avg_gain / avg_loss
df_xg['rsi_raw'] = 100 - (100 / (1 + rs))
df_xg['rsi_signal'] = df_xg['rsi_raw'].shift(1)

# MACD
exp12 = df_xg['Close'].ewm(span=12, adjust=False).mean()
exp26 = df_xg['Close'].ewm(span=26, adjust=False).mean()
df_xg['macd_raw'] = exp12 - exp26
df_xg['macd_signal'] = df_xg['macd_raw'].shift(1)

df_xg = df_xg.dropna()


In [13]:
# Forecast 1, 30, and 180 days ahead

df_xg['target_180'] = df_xg['Close'].shift(-180) / df_xg['Close'] - 1 
df_xg['target_30'] = df_xg['Close'].shift(-30) / df_xg['Close'] - 1 
df_xg['target_1'] = df_xg['Close'].shift(-1) / df_xg['Close'] - 1 

In [14]:
# Split data

X = df_xg.drop(columns=['target_180', 'target_30', 'target_1', 'rsi_raw', 'macd_raw'])
X_train = X.loc[X.index < '2021-01-31']
X_val = X.loc[(X.index >= '2021-01-31') & (X.index < '2022-02-28')]
X_test = X.loc[X.index >= '2022-02-28']

y_180 = df_xg['target_180']
y_train_180 = y_180.loc[y_180.index < '2021-01-31']
y_val_180 = y_180.loc[(y_180.index >= '2021-01-31') & (y_180.index < '2022-02-28')]
y_test_180 = y_180.loc[y_180.index >= '2022-02-28']

y_30 = df_xg['target_30']
y_train_30 = y_30.loc[y_30.index < '2021-01-31']
y_val_30 = y_30.loc[(y_30.index >= '2021-01-31') & (y_30.index < '2022-02-28')]
y_test_30 = y_30.loc[y_30.index >= '2022-02-28']

y_1 = df_xg['target_1']
y_train_1 = y_1.loc[y_1.index < '2021-01-31']
y_val_1 = y_1.loc[(y_1.index >= '2021-01-31') & (y_1.index < '2022-02-28')]
y_test_1 = y_1.loc[y_1.index >= '2022-02-28']


In [15]:
# Train and fit XGBoost 180-day Model

reg_180 = xgb.XGBRegressor(
    n_estimators=2000,
    learning_rate=0.01,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42,
    early_stopping_rounds=100
)

reg_180.fit(
    X_train,
    y_train_180,
    eval_set=[(X_val, y_val_180)],
    verbose=False
)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=100,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.01, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=2000,
             n_jobs=None, num_parallel_tree=None, ...)

In [16]:
# Ranking feature importance

xg_importance = pd.DataFrame(data = reg_180.feature_importances_, index = reg_180.feature_names_in_, columns = ['Importance']).sort_values(by='Importance', ascending=False)

# Create subplots
fig = make_subplots(
    rows=1, cols=1,
    subplot_titles=('XGBoost Feature ranking (180 day ahead)',)
)

fig.add_trace(
    go.Bar(
        x=xg_importance.index,
        y=xg_importance['Importance'],
        marker=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=1, col=1)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=False,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="Importance", col=1)

fig.show()


In [17]:
# Build confidence interval

val_pred = reg_180.predict(X_val)
residuals = y_val_180 - val_pred
residual_std = residuals.std()
ci_multiplier = 1.96  # 95% confidence interval
print("Residual std:", residual_std)

Residual std: 0.06891687215994123


In [18]:
# Plot actual vs predicted price with confidence interval

df_xg['Actual_180_day_Price'] = df_xg['Close'].shift(-180)
pred = reg_180.predict(X_test)

pred_df = pd.DataFrame(
    pred,
    index=X_test.index,
    columns=['Prediction_180']
)

df_xg = df_xg.merge(pred_df, left_index=True, right_index=True, how='left')
df_xg['180_day_Predicted_Price'] = df_xg['Close'] * (1 + df_xg['Prediction_180'])
df_xg['Predicted_Return_Lower'] = df_xg['Prediction_180'] - ci_multiplier * residual_std
df_xg['Predicted_Return_Upper'] = df_xg['Prediction_180'] + ci_multiplier * residual_std
df_xg['Predicted_Price_Lower'] = df_xg['Close'] * (1 + df_xg['Predicted_Return_Lower'])
df_xg['Predicted_Price_Upper'] = df_xg['Close'] * (1 + df_xg['Predicted_Return_Upper'])

# Create subplots
fig = make_subplots(
    rows=1, cols=1,
    subplot_titles=('180-day-ahead Forecast vs Actual Gold Prices',)
    
)

fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['Close'],
        mode='lines',
        name='Actual',
        line=dict(color='green') 
    ),
    row=1, col=1)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=180),  # Shift predicted price 180 days ahead,
        y=df_xg['180_day_Predicted_Price'],
        mode='lines',
        name='Forecast',
        line=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=1, col=1)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=180),
        y=df_xg['Predicted_Price_Upper'],
        mode='lines',
        line=dict(width=0),
        showlegend=False
    ),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=180),
        y=df_xg['Predicted_Price_Lower'],
        mode='lines',
        fill='tonexty',
        fillcolor='rgba(255,20,147,0.2)',
        line=dict(width=0),
        name='95% Confidence Interval'
    ),
    row=1, col=1
)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=True,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="Price", col=1)

# ============================

eval_df = df_xg.loc[X_test.index].copy()
eval_df = eval_df.dropna(subset=['180_day_Predicted_Price','Actual_180_day_Price'])
rmse = np.sqrt(mean_squared_error(eval_df['Actual_180_day_Price'],eval_df['180_day_Predicted_Price']))

mask = ~np.isnan(pred) & ~np.isnan(y_test_180)
rmse_return = np.sqrt(mean_squared_error(pred[mask], y_test_180[mask]))
print("Model Return RMSE:", rmse_return)

# ====== Naive Model =====

eval_df['180_day_Naive_Price'] = eval_df['Close']

naive_rmse = np.sqrt(mean_squared_error(
    eval_df['Actual_180_day_Price'],
    eval_df['180_day_Naive_Price']
))

model_rmse = np.sqrt(mean_squared_error(
    eval_df['Actual_180_day_Price'],
    eval_df['180_day_Predicted_Price']
))

print("Naive RMSE:", naive_rmse)
print("Model RMSE:", model_rmse)

df_xg['180_day_Naive_Price'] = np.nan
df_xg.loc[X_test.index, '180_day_Naive_Price'] = df_xg.loc[X_test.index, 'Close']

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=180),
        y=df_xg['180_day_Naive_Price'],
        mode='lines',
        name='Naive Forecast',
        opacity=0.7,
        line=dict(color='cyan', dash='dash', width=1)
    ),
    row=1, col=1
)

# directional accuracy

eval_df['actual_return'] = eval_df['Actual_180_day_Price'] / eval_df['Close'] - 1
eval_df['pred_return'] = eval_df['180_day_Predicted_Price'] / eval_df['Close'] - 1
direction_accuracy = ( np.sign(eval_df['actual_return']) == np.sign(eval_df['pred_return'])).mean()
print('Direction_accuracy:', direction_accuracy)

# ===== FUTURE FORECAST =====

latest_X = X.iloc[-1:]
future_return = reg_180.predict(latest_X)[0]
future_return_lower = future_return - ci_multiplier * residual_std
future_return_upper = future_return + ci_multiplier * residual_std
latest_price = df_xg['Close'].iloc[-1]
future_price = latest_price * (1 + future_return)
future_price_lower = latest_price * (1 + future_return_lower)
future_price_upper = latest_price * (1 + future_return_upper)
future_date = df_xg.index[-1] + pd.Timedelta(days=180)

# XGBoost 180-day-ahead model
fig.add_trace(
    go.Scatter(
        x=[future_date],
        y=[future_price],
        mode='markers',
        marker=dict(size=6, color='red'),
        name='XGBoost Forecast'
    ),
    row=1, col=1
)

# confidence interval line
fig.add_trace(
    go.Scatter(
        x=[future_date, future_date],
        y=[future_price_lower, future_price_upper],
        mode='lines',
        line=dict(color='gray'),
        name='180-day-ahead 95% CI'
    ),
    row=1, col=1
)

# Naive 180-day-ahead model

naive_future_price = latest_price

fig.add_trace(
    go.Scatter(
        x=[future_date],
        y=[naive_future_price],
        mode='markers',
        marker=dict(size=6, color='cyan'),
        name='Naive Forecast'
    ),
    row=1, col=1
)

fig.show()


Model Return RMSE: 0.20651639409089562
Naive RMSE: 632.9350972835655
Model RMSE: 546.2933319397196
Direction_accuracy: 0.9071782178217822


In [19]:
# Create evaluation dataframe for returns
eval_return_df = pd.DataFrame({
    'Actual_Return': y_test_180,
    'Predicted_Return': pred
}, index=X_test.index)

# Drop NaN if any


eval_return_df = eval_return_df.dropna()

import plotly.graph_objects as go

fig = go.Figure()

# Actual return
fig.add_trace(
    go.Scatter(
        x=eval_return_df.index,
        y=eval_return_df['Actual_Return'],
        mode='lines',
        name='Actual 180-Day Return',
        line=dict(color='cyan', width=1)
    )
)

# Predicted return
fig.add_trace(
    go.Scatter(
        x=eval_return_df.index,
        y=eval_return_df['Predicted_Return'],
        mode='lines',
        name='Predicted 180-Day Return',
        line=dict(color='magenta', width=1)
    )
)

fig.update_layout(
    title="Predicted vs Actual 180-Day Gold Returns",
    xaxis_title="Date",
    yaxis_title="Return",
    template="plotly_dark",
    width=1200,
    height=500
)

fig.show()

In [20]:
# Train and fit XGBoost 30-day Model

reg_30 = xgb.XGBRegressor(
    n_estimators=2000,
    learning_rate=0.01,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42,
    early_stopping_rounds=100
)

reg_30.fit(
    X_train,
    y_train_30,
    eval_set=[(X_val, y_val_30)],
    verbose=False
)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=100,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.01, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=2000,
             n_jobs=None, num_parallel_tree=None, ...)

In [21]:
# Ranking feature importance

xg_importance = pd.DataFrame(data = reg_30.feature_importances_, index = reg_30.feature_names_in_, columns = ['Importance']).sort_values(by='Importance', ascending=False)

# Create subplots
fig = make_subplots(
    rows=1, cols=1,
    subplot_titles=('XGBoost Feature ranking (30 day ahead)',)
)

fig.add_trace(
    go.Bar(
        x=xg_importance.index,
        y=xg_importance['Importance'],
        marker=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=1, col=1)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=False,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="Importance", col=1)

fig.show()


In [22]:
# Build confidence interval

val_pred = reg_30.predict(X_val)
residuals = y_val_30 - val_pred
residual_std = residuals.std()
ci_multiplier = 1.96  # 95% confidence interval
print("Residual std:", residual_std)

Residual std: 0.039863413620116556


In [23]:
# Plot actual vs predicted price with confidence interval

df_xg['Actual_30_day_Price'] = df_xg['Close'].shift(-30)
pred = reg_30.predict(X_test)

pred_df = pd.DataFrame(
    pred,
    index=X_test.index,
    columns=['Prediction_30']
)

df_xg = df_xg.merge(pred_df, left_index=True, right_index=True, how='left')
df_xg['30_day_Predicted_Price'] = df_xg['Close'] * (1 + df_xg['Prediction_30'])
df_xg['Predicted_Return_Lower'] = df_xg['Prediction_30'] - ci_multiplier * residual_std
df_xg['Predicted_Return_Upper'] = df_xg['Prediction_30'] + ci_multiplier * residual_std
df_xg['Predicted_Price_Lower'] = df_xg['Close'] * (1 + df_xg['Predicted_Return_Lower'])
df_xg['Predicted_Price_Upper'] = df_xg['Close'] * (1 + df_xg['Predicted_Return_Upper'])

# Create subplots
fig = make_subplots(
    rows=1, cols=1,
    subplot_titles=('30-day-ahead Forecast vs Actual Gold Prices',)
    
)

fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['Close'],
        mode='lines',
        name='Actual',
        line=dict(color='green') 
    ),
    row=1, col=1)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=30),  # Shift predicted price 180 days ahead,
        y=df_xg['30_day_Predicted_Price'],
        mode='lines',
        name='Forecast',
        line=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=1, col=1)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=30),
        y=df_xg['Predicted_Price_Upper'],
        mode='lines',
        line=dict(width=0),
        showlegend=False
    ),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=30),
        y=df_xg['Predicted_Price_Lower'],
        mode='lines',
        fill='tonexty',
        fillcolor='rgba(255,20,147,0.2)',
        line=dict(width=0),
        name='95% Confidence Interval'
    ),
    row=1, col=1
)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=True,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="Price", col=1)

# ============================

eval_df = df_xg.loc[X_test.index].copy()
eval_df = eval_df.dropna(subset=['30_day_Predicted_Price','Actual_30_day_Price'])
rmse = np.sqrt(mean_squared_error(eval_df['Actual_30_day_Price'],eval_df['30_day_Predicted_Price']))

mask = ~np.isnan(pred) & ~np.isnan(y_test_30)
rmse_return = np.sqrt(mean_squared_error(pred[mask], y_test_30[mask]))
print("Model Return RMSE:", rmse_return)

# ====== Naive Model =====

eval_df['30_day_Naive_Price'] = eval_df['Close']

naive_rmse = np.sqrt(mean_squared_error(
    eval_df['Actual_30_day_Price'],
    eval_df['30_day_Naive_Price']
))

model_rmse = np.sqrt(mean_squared_error(
    eval_df['Actual_30_day_Price'],
    eval_df['30_day_Predicted_Price']
))

print("Naive RMSE:", naive_rmse)
print("Model RMSE:", model_rmse)

df_xg['30_day_Naive_Price'] = np.nan
df_xg.loc[X_test.index, '30_day_Naive_Price'] = df_xg.loc[X_test.index, 'Close']

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=30),
        y=df_xg['30_day_Naive_Price'],
        mode='lines',
        name='Naive Forecast',
        opacity=0.7,
        line=dict(color='cyan', dash='dash', width=1)
    ),
    row=1, col=1
)

# directional accuracy

eval_df['actual_return'] = eval_df['Actual_30_day_Price'] / eval_df['Close'] - 1
eval_df['pred_return'] = eval_df['30_day_Predicted_Price'] / eval_df['Close'] - 1
direction_accuracy = ( np.sign(eval_df['actual_return']) == np.sign(eval_df['pred_return'])).mean()
print('Direction_accuracy:', direction_accuracy)

# ===== FUTURE FORECAST =====

latest_X = X.iloc[-1:]
future_return = reg_30.predict(latest_X)[0]
future_return_lower = future_return - ci_multiplier * residual_std
future_return_upper = future_return + ci_multiplier * residual_std
latest_price = df_xg['Close'].iloc[-1]
future_price = latest_price * (1 + future_return)
future_price_lower = latest_price * (1 + future_return_lower)
future_price_upper = latest_price * (1 + future_return_upper)
future_date = df_xg.index[-1] + pd.Timedelta(days=30)

# XGBoost 30-day-ahead model
fig.add_trace(
    go.Scatter(
        x=[future_date],
        y=[future_price],
        mode='markers',
        marker=dict(size=6, color='red'),
        name='XGBoost Forecast'
    ),
    row=1, col=1
)

# confidence interval line
fig.add_trace(
    go.Scatter(
        x=[future_date, future_date],
        y=[future_price_lower, future_price_upper],
        mode='lines',
        line=dict(color='gray'),
        name='30-day-ahead 95% CI'
    ),
    row=1, col=1
)

# Naive 30-day-ahead model

naive_future_price = latest_price

fig.add_trace(
    go.Scatter(
        x=[future_date],
        y=[naive_future_price],
        mode='markers',
        marker=dict(size=6, color='cyan'),
        name='Naive Forecast'
    ),
    row=1, col=1
)

fig.show()

Model Return RMSE: 0.058050563608957294
Naive RMSE: 187.8945137925878
Model RMSE: 170.21302440682052
Direction_accuracy: 0.6597077244258872


In [24]:
# Create evaluation dataframe for returns
eval_return_df = pd.DataFrame({
    'Actual_Return': y_test_30,
    'Predicted_Return': pred
}, index=X_test.index)

eval_return_df = eval_return_df.dropna()

import plotly.graph_objects as go

fig = go.Figure()

# Actual return
fig.add_trace(
    go.Scatter(
        x=eval_return_df.index,
        y=eval_return_df['Actual_Return'],
        mode='lines',
        name='Actual 30-Day Return',
        line=dict(color='cyan', width=1)
    )
)

# Predicted return
fig.add_trace(
    go.Scatter(
        x=eval_return_df.index,
        y=eval_return_df['Predicted_Return'],
        mode='lines',
        name='Predicted 30-Day Return',
        line=dict(color='magenta', width=1)
    )
)

fig.update_layout(
    title="Predicted vs Actual 30-Day Gold Returns",
    xaxis_title="Date",
    yaxis_title="Return",
    template="plotly_dark",
    width=1200,
    height=500
)

fig.show()

In [25]:
# Train and fit XGBoost 1-day Model

reg_1 = xgb.XGBRegressor(
    n_estimators=2000,
    learning_rate=0.01,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42,
    early_stopping_rounds=100
)

reg_1.fit(
    X_train,
    y_train_1,
    eval_set=[(X_val, y_val_1)],
    verbose=False
)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=100,
             enable_categorical=False, eval_metric=None, feature_types=None,
             feature_weights=None, gamma=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             learning_rate=0.01, max_bin=None, max_cat_threshold=None,
             max_cat_to_onehot=None, max_delta_step=None, max_depth=6,
             max_leaves=None, min_child_weight=None, missing=nan,
             monotone_constraints=None, multi_strategy=None, n_estimators=2000,
             n_jobs=None, num_parallel_tree=None, ...)

In [26]:
# Ranking feature importance

xg_importance = pd.DataFrame(data = reg_1.feature_importances_, index = reg_1.feature_names_in_, columns = ['Importance']).sort_values(by='Importance', ascending=False)

# Create subplots
fig = make_subplots(
    rows=1, cols=1,
    subplot_titles=('XGBoost Feature ranking (1 day ahead)',)
)

fig.add_trace(
    go.Bar(
        x=xg_importance.index,
        y=xg_importance['Importance'],
        marker=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=1, col=1)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=False,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="Importance", col=1)

fig.show()


In [27]:
# Build confidence interval

val_pred = reg_1.predict(X_val)
residuals = y_val_1 - val_pred
residual_std = residuals.std()
ci_multiplier = 1.96  # 95% confidence interval
print("Residual std:", residual_std)

Residual std: 0.009033609483394793


In [28]:
# Plot actual vs predicted price with confidence interval

df_xg['Actual_1_day_Price'] = df_xg['Close'].shift(-1)
pred = reg_1.predict(X_test)

pred_df = pd.DataFrame(
    pred,
    index=X_test.index,
    columns=['Prediction_1']
)

df_xg = df_xg.merge(pred_df, left_index=True, right_index=True, how='left')
df_xg['1_day_Predicted_Price'] = df_xg['Close'] * (1 + df_xg['Prediction_1'])
df_xg['Predicted_Return_Lower'] = df_xg['Prediction_1'] - ci_multiplier * residual_std
df_xg['Predicted_Return_Upper'] = df_xg['Prediction_1'] + ci_multiplier * residual_std
df_xg['Predicted_Price_Lower'] = df_xg['Close'] * (1 + df_xg['Predicted_Return_Lower'])
df_xg['Predicted_Price_Upper'] = df_xg['Close'] * (1 + df_xg['Predicted_Return_Upper'])

# Create subplots
fig = make_subplots(
    rows=1, cols=1,
    subplot_titles=('1-day-ahead Forecast vs Actual Gold Prices',)
    
)

fig.add_trace(
    go.Scatter(
        x=df_xg.index,
        y=df_xg['Close'],
        mode='lines',
        name='Actual',
        line=dict(color='green') 
    ),
    row=1, col=1)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=1),  # Shift predicted price 1 days ahead,
        y=df_xg['1_day_Predicted_Price'],
        mode='lines',
        name='Forecast',
        line=dict(color='rgba(255, 20, 147, 1)') # Neon pink
    ),
    row=1, col=1)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=1),
        y=df_xg['Predicted_Price_Upper'],
        mode='lines',
        line=dict(width=0),
        showlegend=False
    ),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=1),
        y=df_xg['Predicted_Price_Lower'],
        mode='lines',
        fill='tonexty',
        fillcolor='rgba(255,20,147,0.2)',
        line=dict(width=0),
        name='95% Confidence Interval'
    ),
    row=1, col=1
)

# Update layout
fig.update_layout(
    height=500,
    width=1200,
    showlegend=True,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font=dict(color='white')
)

# Update axes
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)
fig.update_yaxes(

    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128,128,128,0.2)',
    zeroline=True,
    zerolinewidth=1,
    zerolinecolor='rgba(128,128,128,0.5)'
)

fig.update_yaxes(title_text="Price", col=1)

# ============================

eval_df = df_xg.loc[X_test.index].copy()
eval_df = eval_df.dropna(subset=['1_day_Predicted_Price','Actual_1_day_Price'])
rmse = np.sqrt(mean_squared_error(eval_df['Actual_1_day_Price'],eval_df['1_day_Predicted_Price']))

mask = ~np.isnan(pred) & ~np.isnan(y_test_1)
rmse_return = np.sqrt(mean_squared_error(pred[mask], y_test_1[mask]))
print("Model Return RMSE:", rmse_return)

# ====== Naive Model =====

eval_df['1_day_Naive_Price'] = eval_df['Close']

naive_rmse = np.sqrt(mean_squared_error(
    eval_df['Actual_1_day_Price'],
    eval_df['1_day_Naive_Price']
))

model_rmse = np.sqrt(mean_squared_error(
    eval_df['Actual_1_day_Price'],
    eval_df['1_day_Predicted_Price']
))

print("Naive RMSE:", naive_rmse)
print("Model RMSE:", model_rmse)

df_xg['1_day_Naive_Price'] = np.nan
df_xg.loc[X_test.index, '1_day_Naive_Price'] = df_xg.loc[X_test.index, 'Close']

fig.add_trace(
    go.Scatter(
        x=df_xg.index + pd.Timedelta(days=1),
        y=df_xg['1_day_Naive_Price'],
        mode='lines',
        name='Naive Forecast',
        opacity=0.7,
        line=dict(color='cyan', dash='dash', width=1)
    ),
    row=1, col=1
)

# directional accuracy

eval_df['actual_return'] = eval_df['Actual_1_day_Price'] / eval_df['Close'] - 1
eval_df['pred_return'] = eval_df['1_day_Predicted_Price'] / eval_df['Close'] - 1
direction_accuracy = ( np.sign(eval_df['actual_return']) == np.sign(eval_df['pred_return'])).mean()
print('Direction_accuracy:', direction_accuracy)

# ===== FUTURE FORECAST =====

latest_X = X.iloc[-1:]
future_return = reg_1.predict(latest_X)[0]
future_return_lower = future_return - ci_multiplier * residual_std
future_return_upper = future_return + ci_multiplier * residual_std
latest_price = df_xg['Close'].iloc[-1]
future_price = latest_price * (1 + future_return)
future_price_lower = latest_price * (1 + future_return_lower)
future_price_upper = latest_price * (1 + future_return_upper)
future_date = df_xg.index[-1] + pd.Timedelta(days=1)

# XGBoost 1-day-ahead model
fig.add_trace(
    go.Scatter(
        x=[future_date],
        y=[future_price],
        mode='markers',
        marker=dict(size=6, color='red'),
        name='XGBoost Forecast'
    ),
    row=1, col=1
)

# confidence interval line
fig.add_trace(
    go.Scatter(
        x=[future_date, future_date],
        y=[future_price_lower, future_price_upper],
        mode='lines',
        line=dict(color='gray'),
        name='1-day-ahead 95% CI'
    ),
    row=1, col=1
)

# Naive 1-day-ahead model

naive_future_price = latest_price

fig.add_trace(
    go.Scatter(
        x=[future_date],
        y=[naive_future_price],
        mode='markers',
        marker=dict(size=6, color='cyan'),
        name='Naive Forecast'
    ),
    row=1, col=1
)

fig.show()

Model Return RMSE: 0.011517240391627142
Naive RMSE: 39.17619273532972
Model RMSE: 39.10411389031321
Direction_accuracy: 0.4387031408308004


In [29]:
# Create evaluation dataframe for returns
eval_return_df = pd.DataFrame({
    'Actual_Return': y_test_1,
    'Predicted_Return': pred
}, index=X_test.index)

eval_return_df = eval_return_df.dropna()

import plotly.graph_objects as go

fig = go.Figure()

# Actual return
fig.add_trace(
    go.Scatter(
        x=eval_return_df.index,
        y=eval_return_df['Actual_Return'],
        mode='lines',
        name='Actual 1-Day Return',
        line=dict(color='cyan', width=1)
    )
)

# Predicted return
fig.add_trace(
    go.Scatter(
        x=eval_return_df.index,
        y=eval_return_df['Predicted_Return'],
        mode='lines',
        name='Predicted 1-Day Return',
        line=dict(color='magenta', width=1)
    )
)

fig.update_layout(
    title="Predicted vs Actual 1-Day Gold Returns",
    xaxis_title="Date",
    yaxis_title="Return",
    template="plotly_dark",
    width=1200,
    height=500
)

fig.show()

### FB Prophet

In [30]:
prophet_df = gold.copy().reset_index()
prophet_df = prophet_df.rename(columns={'Date': 'ds', 'Close': 'y'})

In [31]:
# Split data
test_prophet = prophet_df.iloc[-1000:]
train_prophet = prophet_df.iloc[:-1000]
print(test_prophet.iloc[0]['ds'])

2022-02-28 00:00:00


In [32]:
fbp = Prophet(yearly_seasonality = True, daily_seasonality = False,)
fbp.fit(train_prophet)
future = fbp.make_future_dataframe(periods = 2000)
forecast = fbp.predict(future)

14:53:12 - cmdstanpy - INFO - Chain [1] start processing
14:53:13 - cmdstanpy - INFO - Chain [1] done processing


In [33]:
# Plot Prophet model

fig = plot_plotly(fbp, forecast)

fig.update_layout(
    template="plotly_dark",
    
    xaxis=dict(
        rangeselector=dict(
            bgcolor="rgba(50,50,50,0.8)",   # button background
            activecolor="rgba(150,150,150,0.8)",  # active button color
            font=dict(color="white"),       # button text color
            bordercolor="gray"
        ),
        rangeslider=dict(
            bgcolor="rgba(30,30,30,0.8)"
        )
    ),
    title = 'Prophet forecast vs Actual price'
)

fig.add_trace(
    go.Scatter(
        x=test_prophet['ds'],
        y=test_prophet['y'],
        mode='lines',
        name='Actual price'
    )
)


# Evaluate prophet performace
eval_df = test_prophet.merge(forecast, how = 'left', on = 'ds')
mask =  ~np.isnan(eval_df['y']) & ~np.isnan(eval_df['yhat'])
prophet_rmse = np.sqrt(mean_squared_error(eval_df['y'][mask], eval_df['yhat'][mask]))
print('Prophet Model RMSE:', prophet_rmse)

fig.show()


Prophet Model RMSE: 684.4322448996818
